In [66]:
import pandas as pd
import numpy as np
import warnings 
import nltk
import matplotlib.pyplot as plt
from nltk.tokenize import RegexpTokenizer
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from nltk.tokenize import word_tokenize
import re
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.decomposition import LatentDirichletAllocation
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, hamming_loss
from sklearn.metrics import jaccard_score 
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MultiLabelBinarizer
from gensim.models import LdaModel
from gensim.models.coherencemodel import CoherenceModel
from gensim import corpora
from gensim.corpora import Dictionary
from datetime import datetime

In [2]:
import pyLDAvis
import pyLDAvis.gensim_models

In [3]:
warnings.filterwarnings('ignore')

In [4]:
data =  pd.read_csv('data_processed.csv',  engine = 'python',  on_bad_lines = 'skip')

In [5]:
data.columns

Index(['Id', 'Title', 'Title_tokens', 'Body', 'Body_tokens', 'Tags',
       'Tag_token', 'Score', 'AnswerCount'],
      dtype='object')

In [6]:
data.shape

(50000, 9)

In [7]:
X = data[['Title_tokens', 'Body_tokens','Tag_token','Score', 'AnswerCount']]
y = data[['Tag_token']]

# re tokenisations des variables tockens suite à la lecture csv qui lit champe en string,  mise à jour aussi dans dataframe data. 
X['Title_tokens'] = X['Title_tokens'].apply(lambda x: re.sub('[^a-zA-Z_]', ' ', str(x)))
X['Title_tokens'] = X['Title_tokens'].apply(nltk.word_tokenize)
X['Body_tokens'] = X['Body_tokens'].apply(lambda x: re.sub('[^a-zA-Z_]', ' ', str(x)))
X['Body_tokens'] = X['Body_tokens'].apply(nltk.word_tokenize)
X['Tag_token'] = X['Tag_token'].apply(lambda x: re.sub('[^a-zA-Z_]', ' ', str(x)))
X['Tag_token'] = X['Tag_token'].apply(nltk.word_tokenize)

# Split the Title_tokens into train and test sets
X_train, X_test = train_test_split(X, test_size=0.2, random_state=42)

X_train_title = X_train['Title_tokens']
X_test_title = X_test['Title_tokens']
X_train_body = X_train['Body_tokens']
X_test_body = X_test['Body_tokens']
X_train_tag = X_train['Tag_token']
X_test_tag = X_test['Tag_token']

In [8]:
X_train_title.head()

39087                                  [stored, procedure]
30893                         [run, fly, tomcat, netbeans]
45278    [show, gray, color, view, io, navigation, bar,...
16398    [form, authentication, ticket, decryption, pos...
13653                                    [validation, yii]
Name: Title_tokens, dtype: object

In [9]:
X_test_tag.head()

33553         [javascript, jquery, html, css, tablesorter]
9427               [php, mysql, file, codeigniter, upload]
199      [python, python, x, csv, dictionary, multidime...
12447               [php, net, frameworks, ldap, openldap]
39489    [vue, js, vuejs, datepicker, vue, component, v...
Name: Tag_token, dtype: object

# 3. Modèles non supervisés

Nous utilisons LDA comme le modèle non supervisé.  LDA entrainé est utilisée pour découvrir des sujets cachés dans les nouveaux documents. 
Les mots les plus probables dans ces sujets découverts sont généralement considérés comme les mots-clés les plus pertinents pour le document.

In [10]:
performance_list = []
pyLDAvis.enable_notebook()

In [11]:
train_result = pd.DataFrame(performance_list, columns=['Date', 'Modele', 'nb topics', 'perplexity', 'coherence_score'])
train_result.to_csv('lda_train_result.csv')

# 3.1 Entrainement et nombre de topics

In [13]:
def lda_train(num_topics, X_train):
    # Create a dictionary and bag-of-words representation of the training data
    dictionary = Dictionary(X_train)
    bow_corpus = [dictionary.doc2bow(doc) for doc in X_train]
    
    # Train the LDA model
    lda_model = LdaModel(corpus=bow_corpus, num_topics=num_topics, id2word=dictionary)

    topics = lda_model.get_document_topics(bow_corpus)
    
    #  Visulisation des topics 
#    vis = pyLDAvis.gensim_models.prepare(topic_model=lda_model, corpus=bow_corpus, dictionary=dictionary, mds='mmds', R=30)
    vis = pyLDAvis.gensim_models.prepare(topic_model=lda_model, corpus=bow_corpus, dictionary=dictionary, mds='pcoa', sort_topics=True)
    
    # Calculer la perplexité
    perplexity = lda_model.log_perplexity(bow_corpus)

    # Calculer la cohérence des topics
    coherence_model = CoherenceModel(model=lda_model, texts=X_train, corpus=bow_corpus, coherence='c_v')
    coherence_score = coherence_model.get_coherence()
    
    return perplexity, coherence_score, lda_model, vis

### 3.1.1 Modèle 1: LDA entrainement avec titre

In [14]:
num_topics = 10
perplexity_titre, coherence_score_titre, lda_titre, vis_titre = lda_train(num_topics, X_train_title)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre', num_topics, perplexity_titre, coherence_score_titre]
performance_list.append(y_resultat)
vis_titre

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
8     -0.189938  0.143519       1        1  11.197606
2      0.006521 -0.246810       2        1  10.912089
5      0.193056  0.162983       3        1  10.679295
3     -0.057213  0.068197       4        1  10.431899
6      0.126834 -0.084066       5        1  10.365879
9     -0.201627 -0.033551       6        1   9.734171
4     -0.190958 -0.013270       7        1   9.570858
1      0.152513  0.157238       8        1   9.431576
0      0.138072 -0.154371       9        1   9.224705
7      0.022740  0.000129      10        1   8.451920, topic_info=          Term         Freq        Total Category  logprob  loglift
237     server  1262.000000  1262.000000  Default  30.0000  30.0000
144        sql   977.000000   977.000000  Default  29.0000  29.0000
188      array  1017.000000  1017.000000  Default  28.0000  28.0000
329   function  1093.000000  1093.000000  Default  27.0000  27.0000
77      spring   689.000000   689.000000  Default  26.0000  26.0000
..         ...          ...          ...      ...      ...      ...
229      input   141.395273   477.611276  Topic10  -4.8743   1.2535
687     memory   132.583602   381.057886  Topic10  -4.9387   1.4150
470  different   140.112479   622.242711  Topic10  -4.8835   0.9799
923      model   128.415774   418.676027  Topic10  -4.9706   1.2890
199     result   125.207367   339.678457  Topic10  -4.9959   1.4727

[646 rows x 6 columns], token_table=      Topic      Freq    Term
term                         
783       9  0.993532    able
839       1  0.017543  access
839       2  0.004386  access
839       3  0.712668  access
839       4  0.008771  access
...     ...       ...     ...
341       6  0.310986     xml
341       7  0.001932     xml
341       9  0.025111     xml
341      10  0.005795     xml
5712      1  0.978514    year

[1606 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[9, 3, 6, 4, 7, 10, 5, 2, 1, 8])

In [15]:
num_topics = 20
perplexity_titre, coherence_score_titre, lda_titre, vis_titre = lda_train(num_topics, X_train_title)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre', num_topics, perplexity_titre, coherence_score_titre]
performance_list.append(y_resultat)
vis_titre

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
13    -0.086106 -0.084532       1        1  6.244788
7      0.140710 -0.182115       2        1  6.056913
6      0.168474  0.118471       3        1  5.671204
9      0.003905  0.158889       4        1  5.593959
8     -0.145848 -0.136842       5        1  5.287286
2      0.015711  0.038743       6        1  5.040797
19    -0.089502  0.095776       7        1  5.015164
4      0.149257  0.127579       8        1  5.013074
15    -0.121341 -0.030092       9        1  4.991367
11     0.079001 -0.046670      10        1  4.932497
16    -0.120921  0.145257      11        1  4.926221
10     0.168035 -0.032821      12        1  4.900882
1      0.143654 -0.045679      13        1  4.834801
17    -0.096615 -0.196934      14        1  4.723483
3     -0.101372  0.127985      15        1  4.660509
5     -0.168984 -0.017528      16        1  4.626145
18    -0.007316 -0.087295      17        1  4.585357
0      0.069541 -0.070201      18        1  4.534352
12     0.054415 -0.017496      19        1  4.367055
14    -0.054698  0.135504      20        1  3.994147, topic_info=        Term         Freq        Total Category  logprob  loglift
117    image  1315.000000  1315.000000  Default  30.0000  30.0000
188    array  1105.000000  1105.000000  Default  29.0000  29.0000
92   android  1292.000000  1292.000000  Default  28.0000  28.0000
78   working  1038.000000  1038.000000  Default  27.0000  27.0000
212     list   930.000000   930.000000  Default  26.0000  26.0000
..       ...          ...          ...      ...      ...      ...
417   ubuntu    97.468300   123.418324  Topic20  -4.4968   2.9843
261     java   124.929474  1226.589223  Topic20  -4.2486   0.9361
130  project    73.776172   482.379739  Topic20  -4.7753   1.3426
77    spring    73.859474   750.519563  Topic20  -4.7742   0.9017
91       way    66.191038   777.952349  Topic20  -4.8838   0.7562

[995 rows x 6 columns], token_table=      Topic      Freq     Term
term                          
783       9  0.987511     able
839       2  0.043782   access
839       4  0.029851   access
839       6  0.001990   access
839       8  0.003980   access
...     ...       ...      ...
341      16  0.975274      xml
341      19  0.001813      xml
341      20  0.001813      xml
1284      9  0.980454  youtube
1686      2  0.968952     zoom

[2369 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[14, 8, 7, 10, 9, 3, 20, 5, 16, 12, 17, 11, 2, 18, 4, 6, 19, 1, 13, 15])

In [16]:
num_topics = 30
perplexity_titre, coherence_score_titre, lda_titre, vis_titre = lda_train(num_topics, X_train_title)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre', num_topics, perplexity_titre, coherence_score_titre]
performance_list.append(y_resultat)
vis_titre

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
22    -0.038687 -0.212647       1        1  4.629846
10     0.206427  0.103163       2        1  4.423804
5     -0.054424  0.044965       3        1  3.880076
11    -0.069415  0.155488       4        1  3.838569
7      0.048457 -0.076072       5        1  3.786451
19    -0.158348 -0.109292       6        1  3.699626
6      0.148294  0.025641       7        1  3.664292
17     0.174307 -0.032212       8        1  3.502042
12    -0.146169  0.181899       9        1  3.499449
0     -0.086327  0.040041      10        1  3.464022
26     0.117129  0.107727      11        1  3.433110
25    -0.044972 -0.052783      12        1  3.415008
8     -0.084625  0.059792      13        1  3.383903
21    -0.140127 -0.063484      14        1  3.382870
28     0.017179 -0.036770      15        1  3.298827
15     0.001239 -0.094334      16        1  3.278874
9     -0.042262  0.112637      17        1  3.203839
3     -0.038671 -0.129850      18        1  3.125173
1      0.133935  0.106990      19        1  3.109379
24     0.038601 -0.046650      20        1  3.106434
16    -0.202421  0.159190      21        1  3.036598
4      0.006523 -0.008204      22        1  3.013878
20     0.120102  0.073087      23        1  2.950869
18     0.052983 -0.069301      24        1  2.941294
13    -0.013325 -0.068365      25        1  2.936908
14     0.028137 -0.036020      26        1  2.910403
29     0.008447 -0.074975      27        1  2.844803
27    -0.002415 -0.086317      28        1  2.780621
2      0.030524 -0.023306      29        1  2.770612
23    -0.010094  0.049960      30        1  2.688418, topic_info=           Term         Freq        Total Category  logprob  loglift
237      server  1329.000000  1329.000000  Default  30.0000  30.0000
186      object  1206.000000  1206.000000  Default  29.0000  29.0000
399      window  1109.000000  1109.000000  Default  28.0000  28.0000
45       string  1104.000000  1104.000000  Default  27.0000  27.0000
188       array  1103.000000  1103.000000  Default  26.0000  26.0000
...         ...          ...          ...      ...      ...      ...
719   duplicate   146.060566   151.324224  Topic30  -3.6964   3.5808
309   hibernate   159.842042   166.520015  Topic30  -3.6063   3.5753
591   attribute   307.455212   325.989187  Topic30  -2.9521   3.5577
1996      first   246.452078   274.299748  Topic30  -3.1733   3.5092
565    facebook   113.631338   179.420934  Topic30  -3.9475   3.1594

[1223 rows x 6 columns], token_table=      Topic      Freq     Term
term                          
783      28  0.953791     able
783      29  0.025434     able
839       4  0.016286   access
839       5  0.018322   access
839       6  0.596490   access
...     ...       ...      ...
2041     16  0.967301    xpath
21       15  0.987101      yii
1284     12  0.988903  youtube
2437     26  0.981328     zend
1686     10  0.981675     zoom

[2475 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[23, 11, 6, 12, 8, 20, 7, 18, 13, 1, 27, 26, 9, 22, 29, 16, 10, 4, 2, 25, 17, 5, 21, 19, 14, 15, 30, 28, 3, 24])

In [17]:
num_topics = 50
perplexity_titre, coherence_score_titre, lda_titre, vis_titre = lda_train(num_topics, X_train_title)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre', num_topics, perplexity_titre, coherence_score_titre]
performance_list.append(y_resultat)
vis_titre

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
3     -0.139790 -0.140197       1        1  2.816117
28     0.097792 -0.049562       2        1  2.684364
34    -0.033995 -0.053887       3        1  2.545464
38    -0.145912 -0.139775       4        1  2.492561
18    -0.002307  0.084510       5        1  2.485237
29     0.087867 -0.029335       6        1  2.249059
35    -0.005816 -0.152914       7        1  2.245616
17     0.076167 -0.002631       8        1  2.238951
36    -0.103173  0.072881       9        1  2.229225
46    -0.094470  0.019630      10        1  2.228050
27     0.051740 -0.105174      11        1  2.214589
26     0.245715 -0.036874      12        1  2.212772
31    -0.087777 -0.063933      13        1  2.162622
13    -0.035688  0.175727      14        1  2.161914
5     -0.039749 -0.000036      15        1  2.159626
45    -0.053362  0.144997      16        1  2.152658
2      0.000018  0.076900      17        1  2.148063
11    -0.010449 -0.061957      18        1  2.144775
1     -0.010793 -0.043380      19        1  2.139677
22    -0.090835 -0.097913      20        1  2.097020
25     0.089837  0.002869      21        1  2.088782
42     0.029672 -0.036380      22        1  2.076403
43    -0.008499 -0.030135      23        1  2.029732
32     0.068450  0.127847      24        1  2.022534
10     0.056200 -0.078146      25        1  2.008699
4     -0.063935  0.128484      26        1  1.968377
16    -0.119233 -0.024167      27        1  1.966155
9     -0.023440 -0.002343      28        1  1.957525
12    -0.099594 -0.052930      29        1  1.956095
6      0.146064 -0.024027      30        1  1.944884
33    -0.001092  0.012401      31        1  1.916764
15    -0.058008 -0.078011      32        1  1.904296
47    -0.025981  0.062539      33        1  1.887291
41    -0.039599  0.098882      34        1  1.880516
37    -0.023899  0.047326      35        1  1.852780
8      0.097391 -0.046728      36        1  1.822059
30    -0.036801 -0.049617      37        1  1.814289
44     0.046119  0.013523      38        1  1.808557
23    -0.018725 -0.010542      39        1  1.779269
7      0.012550  0.121178      40        1  1.778254
21     0.082890 -0.024861      41        1  1.748600
48    -0.004098  0.035380      42        1  1.693340
49     0.039445  0.072552      43        1  1.676307
20     0.004630 -0.027929      44        1  1.616980
14     0.029655  0.107165      45        1  1.583295
39    -0.010588  0.000201      46        1  1.550619
0     -0.001602  0.026351      47        1  1.516194
40    -0.021756  0.048536      48        1  1.499892
19     0.180383 -0.063654      49        1  1.448683
24    -0.031618  0.047158      50        1  1.394468, topic_info=          Term         Freq        Total Category  logprob  loglift
186     object  1310.000000  1310.000000  Default  30.0000  30.0000
117      image  1335.000000  1335.000000  Default  29.0000  29.0000
209        app  1187.000000  1187.000000  Default  28.0000  28.0000
237     server  1330.000000  1330.000000  Default  27.0000  27.0000
188      array  1101.000000  1101.000000  Default  26.0000  26.0000
...        ...          ...          ...      ...      ...      ...
539      oledb    15.790292    16.916198  Topic50  -5.2646   4.2038
1720     sonar    14.186431    15.298222  Topic50  -5.3717   4.1972
1240     later    13.737386    14.863465  Topic50  -5.4039   4.1939
1834  altering    12.853799    13.965590  Topic50  -5.4704   4.1897
38      python    13.307302  1315.235919  Topic50  -5.4357  -0.3208

[1667 rows x 6 columns], token_table=      Topic      Freq      Term
term                           
783      26  0.982094      able
1804     25  0.973568  absolute
456      11  0.946920    accept
839       7  0.985279    access
839      28  0.002079    access
...     ...       ...       ...
1284     47  0.984892   youtube
2437      1  0.971968      zend
1852     33  0.960054      

### 3.1.2 Modèle 2: LDA entrainement avec titre + body

In [18]:
X_train_merged = X_train_title + X_train_body

In [19]:
X_train_merged.head()

39087    [stored, procedure, function, calling, stored,...
30893    [run, fly, tomcat, netbeans, maven, web, proje...
45278    [show, gray, color, view, io, navigation, bar,...
16398    [form, authentication, ticket, decryption, pos...
13653    [validation, yii, validation, yii, advanced, p...
dtype: object

In [20]:
X_train_title.head()

39087                                  [stored, procedure]
30893                         [run, fly, tomcat, netbeans]
45278    [show, gray, color, view, io, navigation, bar,...
16398    [form, authentication, ticket, decryption, pos...
13653                                    [validation, yii]
Name: Title_tokens, dtype: object

In [21]:
X_train_body.head()

39087    [function, calling, stored, procedure, execute...
30893    [maven, web, project, netbeans, eclipse, refer...
45278    [written, test, ipad, app, contains, split, vi...
16398    [php, developer, almost, nothing, net, asked, ...
13653    [validation, yii, advanced, parent_id, creatin...
Name: Body_tokens, dtype: object

In [22]:
num_topics = 10
perplexity_merged, coherence_score_merged, lda_merged, vis_merged = lda_train(num_topics, X_train_merged)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre et body', num_topics, perplexity_merged, coherence_score_merged]
performance_list.append(y_resultat)
vis_merged

PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
3      0.102811 -0.134270       1        1  12.775265
4     -0.133141 -0.073683       2        1  12.367355
6      0.042593  0.097995       3        1  12.243980
1      0.093344  0.085892       4        1  11.942389
8      0.187752  0.065392       5        1  11.551848
5     -0.086843  0.031323       6        1   9.092382
2     -0.126174  0.123507       7        1   8.728973
0      0.031483  0.031160       8        1   7.974430
9      0.035942 -0.200002       9        1   7.220805
7     -0.147768 -0.027315      10        1   6.102574, topic_info=        Term         Freq        Total Category  logprob  loglift
806     java  7541.000000  7541.000000  Default  30.0000  30.0000
419     page  8935.000000  8935.000000  Default  29.0000  29.0000
106      php  5110.000000  5110.000000  Default  28.0000  28.0000
129    image  8689.000000  8689.000000  Default  27.0000  27.0000
101     form  5473.000000  5473.000000  Default  26.0000  26.0000
..       ...          ...          ...      ...      ...      ...
12    return   661.032919  4826.526338  Topic10  -5.2681   0.8084
244    class   703.988747  9800.262534  Topic10  -5.2052   0.1631
437   header   588.833871  2169.093648  Topic10  -5.3838   1.4925
237   string   644.325101  5567.276536  Topic10  -5.2937   0.6400
6    getting   590.669084  4919.478561  Topic10  -5.3807   0.6768

[863 rows x 6 columns], token_table=      Topic      Freq      Term
term                           
3242      4  0.963965  abstract
3242      6  0.024404  abstract
3242     10  0.008135  abstract
146       1  0.005437    access
146       2  0.288410    access
...     ...       ...       ...
2151      6  0.003086   youtube
2151      8  0.018518   youtube
3030      1  0.045298      zone
3030      7  0.022649      zone
3030      9  0.928618      zone

[3470 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[4, 5, 7, 2, 9, 6, 3, 1, 10, 8])

In [23]:
num_topics = 20
perplexity_merged, coherence_score_merged, lda_merged, vis_merged = lda_train(num_topics, X_train_merged)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre et body', num_topics, perplexity_merged, coherence_score_merged]
performance_list.append(y_resultat)
pyLDAvis.display(vis_merged)

In [24]:
num_topics = 30
perplexity_merged, coherence_score_merged, lda_merged, vis_merged = lda_train(num_topics, X_train_merged)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre et body', num_topics, perplexity_merged, coherence_score_merged]
performance_list.append(y_resultat)
pyLDAvis.display(vis_merged)

In [25]:
num_topics = 50
perplexity_merged, coherence_score_merged, lda_merged, vis_merged = lda_train(num_topics, X_train_merged)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre et body', num_topics, perplexity_merged, coherence_score_merged]
performance_list.append(y_resultat)
pyLDAvis.display(vis_merged)

Nous sélectionnons le model avec 20 topics avec titre

### 3.1.3  Modèle 3: LDA entrainement avec titre & tag et body

In [26]:
def lda_train_tag(num_topics, dictionary, X_train):
    # Create a dictionary and bag-of-words representation of the training data
    # dictionary = Dictionary(X_train)
    bow_corpus = [dictionary.doc2bow(doc) for doc in X_train]
    
    # Train the LDA model
    lda_model = LdaModel(corpus=bow_corpus, num_topics=num_topics, id2word=dictionary)

    topics = lda_model.get_document_topics(bow_corpus)
    
    #  Visulisation des topics 
#    vis = pyLDAvis.gensim_models.prepare(topic_model=lda_model, corpus=bow_corpus, dictionary=dictionary, mds='mmds', R=30)
    vis = pyLDAvis.gensim_models.prepare(topic_model=lda_model, corpus=bow_corpus, dictionary=dictionary, mds='pcoa', sort_topics=True)
    
    # Calculer la perplexité
    perplexity = lda_model.log_perplexity(bow_corpus)

    # Calculer la cohérence des topics
    coherence_model = CoherenceModel(model=lda_model, texts=X_train, corpus=bow_corpus, coherence='c_v')
    coherence_score = coherence_model.get_coherence()
    
    return perplexity, coherence_score, lda_model, vis

In [27]:
# Create a set of tokens from X_train_title and X_train_tag
title_tokens_set = set([token for tokens in X_train_title for token in tokens])
tag_tokens_set = set([token for tokens in X_train_tag for token in tokens])

# Get the common tokens that appear in both sets
X_train_union = title_tokens_set.intersection(tag_tokens_set)

train_dictionary_tag = Dictionary([list(X_train_union)])

In [28]:
num_topics = 10
perplexity_tag, coherence_score_tag, lda_tag, vis_tag = lda_train_tag(num_topics, train_dictionary_tag, X_train_merged)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre&tag + body', num_topics, perplexity_tag, coherence_score_tag]
performance_list.append(y_resultat)
pyLDAvis.display(vis_tag)

In [29]:
num_topics = 20
perplexity_tag, coherence_score_tag, lda_tag, vis_tag = lda_train_tag(num_topics, train_dictionary_tag, X_train_merged)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre&tag + body', num_topics, perplexity_tag, coherence_score_tag]
performance_list.append(y_resultat)
pyLDAvis.display(vis_tag)

In [30]:
num_topics = 30
perplexity_tag, coherence_score_tag, lda_tag, vis_tag = lda_train_tag(num_topics, train_dictionary_tag, X_train_merged)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre&tag + body', num_topics, perplexity_tag, coherence_score_tag]
performance_list.append(y_resultat)
pyLDAvis.display(vis_tag)

In [31]:
num_topics = 50
perplexity_tag, coherence_score_tag, lda_tag, vis_tag = lda_train_tag(num_topics, train_dictionary_tag, X_train_merged)
current_datetime = datetime.now()
formatted_datetime = current_datetime.strftime("%Y-%m-%d %H:%M:%S")
y_resultat = [formatted_datetime, 'lda train avec titre&tag + body', num_topics, perplexity_tag, coherence_score_tag]
performance_list.append(y_resultat)
pyLDAvis.display(vis_tag)

### 3.1.4 LDA entrainement avec titre pour fit et titre+body pour transform

In Gensim, the topic modeling models such as LdaModel do not have separate fit and transform methods like in some other machine learning libraries. Instead, the training and transformation steps are combined into a single process.

### 3.1.5 Example des topics découverts 

In [32]:
num_topics = 10

In [33]:
# Create a dictionary and bag-of-words representation of the training data, modèle 1: 
train_dictionary = Dictionary(X_train_title)
train_bow_corpus = [train_dictionary.doc2bow(doc) for doc in X_train_title]

# Train LDA model with 10 topics
lda_model = LdaModel(corpus=train_bow_corpus, num_topics=num_topics, id2word=train_dictionary)

# topics distribution pour chaque docuement dans X_train_title
train_topics_distribution = lda_model.get_document_topics(train_bow_corpus)

In [34]:
# les 10 topics découverts avec les 8 top words
topics = lda_model.print_topics(num_words=8)
for topic in topics:
    words = topic[1].split('+')
    words = [word.split('*')[1].replace('"', '').strip() for word in words]
    print(words)

['json', 'object', 'spring', 'xml', 'model', 'attribute', 'mvc', 'character']
['array', 'class', 'element', 'jquery', 'list', 'cs', 'input', 'type']
['working', 'view', 'page', 'io', 'app', 'load', 'web', 'button']
['rail', 'studio', 'visual', 'problem', 'test', 'ruby', 'query', 'spring']
['string', 'text', 'sql', 'update', 'convert', 'server', 'button', 'excel']
['database', 'server', 'php', 'asp', 'mysql', 'ajax', 'core', 'access']
['find', 'one', 'another', 'two', 'module', 'video', 'swift', 'inside']
['column', 'different', 'row', 'way', 'python', 'issue', 'table', 'query']
['google', 'api', 'request', 'app', 'key', 'project', 'user', 'http']
['function', 'image', 'method', 'call', 'size', 'possible', 'framework', 'read']


In [35]:
# afficher les probabilité des topics des documents
for i in range(2):
    print(f"Document {i+1} topic distribution:")
    for topic, prob in train_topics_distribution[i]:
        print(f"Topic {topic}: {prob}")
    print()

Document 1 topic distribution:
Topic 0: 0.03333396837115288
Topic 1: 0.03333396837115288
Topic 2: 0.03333396837115288
Topic 3: 0.03333396837115288
Topic 4: 0.6999942660331726
Topic 5: 0.033333975821733475
Topic 6: 0.03333396837115288
Topic 7: 0.033333975821733475
Topic 8: 0.03333396837115288
Topic 9: 0.03333396837115288

Document 2 topic distribution:
Topic 0: 0.020003991201519966
Topic 1: 0.21995021402835846
Topic 2: 0.6200016140937805
Topic 3: 0.020011788234114647
Topic 4: 0.020005011931061745
Topic 5: 0.0200066976249218
Topic 6: 0.020006725564599037
Topic 7: 0.02000381425023079
Topic 8: 0.020006289705634117
Topic 9: 0.02000381238758564



## 3.2 prédiction de topics et les mots

In [36]:
def predit_word(num_topics, X_train, X_test):
    # Prédict la topics distribution for each document in the test set X_test_title
    train_dictionary = Dictionary(X_train)
    train_bow_corpus = [train_dictionary.doc2bow(doc) for doc in X_train]
    
    # Train the LDA model
    lda_model = LdaModel(corpus=train_bow_corpus, num_topics=num_topics, id2word=train_dictionary)
    
    # création bow pour X_test_title avec les dictionary train  (avec test_body et option)    
    test_bow_corpus = [train_dictionary.doc2bow(doc) for doc in X_test]
    # Prédiction des distributions de sujets (topics) pour X_test
    test_topics_distributions = lda_model[test_bow_corpus] 
    
    # Extract keywords from the inferred topic distributions
    test_keywords = []
    for doc_topics in test_topics_distributions:       
    # trier les topics par la probailité en order décroissant (x[1] de doc_topics)
        sorted_topics = sorted(doc_topics, key=lambda x: x[1], reverse=True)
    # extraire le premier mot clé des top topics 
        top_keywords = [train_dictionary[word_id] for word_id, _ in sorted_topics[:10]]  # Adjust the number of keywords as needed
        test_keywords.append(top_keywords)
    return test_keywords

In [37]:
def predit_word_full(num_topics, X_train, X_test):
    # Prédict la topics distribution for each document in the test set X_test_title
    train_dictionary = Dictionary(X_train)
    train_bow_corpus = [train_dictionary.doc2bow(doc) for doc in X_train]
    
    # Train the LDA model
    lda_model = LdaModel(corpus=train_bow_corpus, num_topics=num_topics, id2word=train_dictionary)
    
    # création bow pour X_test_title avec les dictionary train  (avec test_body et option)    
    test_bow_corpus = [train_dictionary.doc2bow(doc) for doc in X_test]
    test_topics_distributions = lda_model[test_bow_corpus] 

    #print("test_bow_corpus = ", test_bow_corpus)
    #print("test_topics_distributions = ", test_topics_distributions)
    
    # Extract keywords from the inferred topic distributions
    test_keywords = []
    for doc_topics in test_topics_distributions:       
    # trier les topics par la probailité en order décroissant (x[1] de doc_topics)
        sorted_topics = sorted(doc_topics, key=lambda x: x[1], reverse=True)
    # extraire le premier mot clé des top topics 
        top_keywords = [train_dictionary[word_id] for word_id, _ in sorted_topics[:10]]  # Adjust the number of keywords as needed
        test_keywords.append(top_keywords)
    return test_keywords, train_dictionary, lda_model

### 3.2.1 Prediction avec modèle 1 

In [38]:
num_topics = 20

In [39]:
test_keywords_m1 = predit_word(num_topics, X_train_title, X_test_title)

In [40]:
print(test_keywords_m1[:5])

[['show', 'netbeans', 'procedure', 'stored', 'fly', 'run', 'tomcat', 'bar', 'color', 'gray'], ['possible', 'navigation', 'io', 'netbeans', 'tomcat', 'php'], ['navigation', 'gray', 'view'], ['form', 'procedure', 'netbeans', 'stored', 'fly', 'run', 'tomcat', 'bar', 'color', 'gray'], ['bar', 'stored', 'ticket']]


In [41]:
test_keywords_m1, train_dictionary, lda_model = predit_word_full(num_topics, X_train_title, X_test_title)

In [42]:
print(test_keywords_m1[:5])

[['uisplitviewcontroller', 'view', 'procedure', 'stored', 'fly', 'netbeans', 'run', 'tomcat', 'bar', 'color'], ['color', 'bar', 'view', 'procedure', 'decryption', 'possible'], ['uisplitviewcontroller', 'stored', 'ticket', 'view'], ['gray', 'form', 'authentication', 'decryption', 'procedure', 'stored', 'fly', 'netbeans', 'run', 'tomcat'], ['run', 'php', 'show']]


In [43]:
import pickle

with open('lda_model.pkl', 'wb') as model_file:
    pickle.dump(lda_model, model_file)
with open('train_dictionary.pkl', 'wb') as dictionary_file:
    pickle.dump(train_dictionary, dictionary_file)    

### 3.2.2 Prediction avec modèle 2 

In [70]:
num_topics = 10

In [71]:
test_keywords_m2, train_dictionary2, lda_model2 = predit_word_full(num_topics, X_train_title + X_train_body,  X_test_title + X_test_body)

In [45]:
#test_keywords_m2 = predit_word(num_topics, X_train_title + X_train_body,  X_test_title + X_test_body)

In [72]:
with open('lda_model2.pkl', 'wb') as model_file:
    pickle.dump(lda_model, model_file)
with open('train_dictionary2.pkl', 'wb') as dictionary_file:
    pickle.dump(train_dictionary, dictionary_file) 

In [73]:
print(test_keywords_m2[:5])

[['fine', 'getting', 'calling', 'keep'], ['execute', 'keep', 'getting', 'calling'], ['fine', 'keep', 'function', 'getting'], ['although', 'correct', 'execute', 'calling'], ['parameter', 'getting', 'keep']]


### 3.2.2 Prediction avec modèle 3

In [47]:
def predit_word_tag(num_topics, train_dictionary, X_train, X_test):
    # Prédict la topics distribution for each document in the test set X_test_title
    # train_dictionary = Dictionary(X_train)
    train_bow_corpus = [train_dictionary.doc2bow(doc) for doc in X_train]
    
    # Train the LDA model
    lda_model = LdaModel(corpus=train_bow_corpus, num_topics=num_topics, id2word=train_dictionary)
    
    # création bow pour X_test_title avec les dictionary train  (avec test_body et option)    
    test_bow_corpus = [train_dictionary.doc2bow(doc) for doc in X_test]
    test_topics_distributions = lda_model[test_bow_corpus] 
    
    # Extract keywords from the inferred topic distributions
    test_keywords = []
    for doc_topics in test_topics_distributions:       
    # trier les topics par la probailité en order décroissant (x[1] de doc_topics)
        sorted_topics = sorted(doc_topics, key=lambda x: x[1], reverse=True)
    # extraire le premier mot clé des top topics 
        top_keywords = [train_dictionary[word_id] for word_id, _ in sorted_topics[:10]]  # Adjust the number of keywords as needed
        test_keywords.append(top_keywords)
    return test_keywords

In [48]:
# Create a set of tokens from X_train_title and X_train_tag
title_tokens_set = set([token for tokens in X_train_title for token in tokens])
tag_tokens_set = set([token for tokens in X_train_tag for token in tokens])

# Get the common tokens that appear in both sets
X_train_union = title_tokens_set.intersection(tag_tokens_set)

train_dictionary_tag = Dictionary([list(X_train_union)])

In [49]:
num_topics = 10

In [50]:
test_keywords_m3 = predit_word_tag(num_topics, train_dictionary_tag, X_train_title, X_test_title)

In [51]:
print(test_keywords_m3[:5])

[['abstraction', 'acceptance', 'abi', 'abide', 'absolute', 'accelerometer', 'abstract', 'abort', 'acceleration', 'aar'], ['abstraction', 'abort', 'acceptance', 'aar', 'abstract', 'accelerometer', 'abide', 'absolute', 'abi', 'acceleration'], ['absolute', 'acceptance', 'abide', 'acceleration', 'accelerometer', 'aar', 'abstraction', 'abort', 'abi', 'abstract'], ['acceleration', 'acceptance', 'abort', 'abi', 'accelerometer', 'absolute', 'aar', 'abide', 'abstract', 'abstraction'], ['acceleration', 'acceptance', 'abstract', 'aar', 'absolute', 'abort', 'abstraction', 'accelerometer', 'abide', 'abi']]


## 3.3 Mesure de prediction

In [52]:
def prediction_couverture(predits, reels): 

    # Convertir les colonnes des dataframes en listes de tokens
    mots_cles_reels = reels.tolist()  # convert token to list de strings
    mots_cles_predits = predits

    # Compteur de mots clés réels correctement prédits
    mots_cles_corrects = 0

    # Parcourir les mots clés réels
    for mots_reels in mots_cles_reels:  # pour chaque document
        for mot_reel in mots_reels:     # chaque mot reel du document
        # si un mot réel est parmi les mots prédits
            if any(mot_reel in mots_predits for mots_predits in mots_cles_predits):
                mots_cles_corrects += 1
                break

    # Calculer le taux de couverture des tags réels
    taux_couverture = mots_cles_corrects / len(mots_cles_reels) * 100

    # Afficher le taux de couverture des tags réels
    print("Taux de couverture des tags réels :", taux_couverture, "%")
    return taux_couverture

In [53]:
couverture_m1 = prediction_couverture(test_keywords_m1,X_test['Tag_token'])

Taux de couverture des tags réels : 10.93 %


In [74]:
couverture_m2 = prediction_couverture(test_keywords_m2,X_test['Tag_token'])

Taux de couverture des tags réels : 11.959999999999999 %


In [55]:
couverture_m3 = prediction_couverture(test_keywords_m3,X_test['Tag_token'])

Taux de couverture des tags réels : 0.2 %


In [67]:
def classification_perm_words(y_test, y_pred) : 
    
    mlb = MultiLabelBinarizer()

    # Convertir les étiquettes en format binaire
    y_test_bin = mlb.fit_transform(y_test)
    y_pred_bin = mlb.transform(y_pred)
    
    # Calculer le score Jaccard pour mesurer la similarité entre deux ensembles
    jaccard = jaccard_score(y_test_bin, y_pred_bin, average='micro')
    # Calculer l'exactitude des prédictions
    accuracy = accuracy_score(y_test_bin, y_pred_bin)
    # Calculer la précision macro-moyenne
    precision = precision_score(y_test_bin, y_pred_bin, average='micro')
    # Calculer le rappel micro-moyen
    recall = recall_score(y_test_bin, y_pred_bin, average='micro')
    # Calculer le score F1 macro-moyen
    f1 = f1_score(y_test_bin, y_pred_bin, average='micro')
    resultat = [jaccard, accuracy, precision,recall, f1]
    return resultat 

In [68]:
perf_m1 = classification_perm_words(test_keywords_m1,X_test['Tag_token'])
print(perf_m1)

[0.0030796425957382166, 0.0, 0.19928507596067918, 0.003118226945396071, 0.006140375030977229]


In [75]:
perf_m2 = classification_perm_words(test_keywords_m2,X_test['Tag_token'])
print(perf_m2)

[0.011569367799399748, 0.0, 0.39733998337489607, 0.011776009460225173, 0.02287409676030052]
